Yingshu Wang 100614552

Data from https://www.kaggle.com/thomaskonstantin/top-270-rated-computer-science-programing-books
#Top 270 Computer Science / Programing Books
High rated book information in the field of computer science and programing

What kind of design can lead to the best rating programing books?
The purpose of the document is help the designer and writer to understand the global book market and the way to produce the high rating books.

In [146]:
!pip install sweetviz

#install sweetviz

In [147]:
import pandas as pd
import numpy as np
import sweetviz as sv

In [148]:
book = pd.read_csv('prog_book.csv')
#read data

In [150]:
book.shape 
display(book)
#print all data

Rating Reviews  ...                   Type       Price
0      4.17   3,829  ...              Hardcover    9.323529
1      4.01   1,406  ...              Hardcover   11.000000
2      3.33       0  ...         Kindle Edition   11.267647
3      3.97   1,658  ...              Hardcover   12.873529
4      4.06   1,325  ...         Kindle Edition   13.164706
..      ...     ...  ...                    ...         ...
266    3.76       0  ...              Hardcover  203.108823
267    3.94      22  ...              Paperback  212.097059
268    4.49      36  ...  Boxed Set - Hardcover  220.385294
269    4.77       4  ...              Hardcover  220.385294
270    3.84       5  ...              Hardcover  235.650000

[271 rows x 7 columns]

In [151]:
book_data= book.loc[:,['Rating', 'Book_title','Number_Of_Pages', 'Type','Price']].dropna()
display(book_data)

#collect useful data

Rating  ...       Price
0      4.17  ...    9.323529
1      4.01  ...   11.000000
2      3.33  ...   11.267647
3      3.97  ...   12.873529
4      4.06  ...   13.164706
..      ...  ...         ...
266    3.76  ...  203.108823
267    3.94  ...  212.097059
268    4.49  ...  220.385294
269    4.77  ...  220.385294
270    3.84  ...  235.650000

[271 rows x 5 columns]

In [152]:
report = sv.analyze(book_data)

:FEATURES DONE:                    |█████████████████████| [100%]   00:01  -> (00:00 left)
:PAIRWISE DONE:                    |█████████████████████| [100%]   00:00  -> (00:00 left)


Creating Associations graph... DONE!


In [153]:
report.show_html()

Report SWEETVIZ_REPORT.html was generated! NOTEBOOK/COLAB USERS: no browser will pop up, the report is saved in your notebook/colab files.


#Histogram

In [154]:

#Histogram graph showing its number of pages, rating and price based on different book Cover Types 
temp = book_data.loc[:,['Number_Of_Pages','Rating','Price']]
visualizable_feature_names = temp.columns[0:3] #

num_visualizable_features = len(visualizable_feature_names)
labels = book_data['Type'].unique()

import plotly.graph_objects as go

fig_hist = []
for i, feature_name in enumerate(visualizable_feature_names):
    fig_hist.append(go.Figure())
    for label in labels:
        fig_hist[i].add_trace(go.Histogram(x=book_data[book_data["Type"]==label][feature_name], name=label))
    fig_hist[i].update_layout(height=400, width=800, title_text=feature_name)
    fig_hist[i].update_layout(barmode='overlay')
    fig_hist[i].update_traces(opacity=0.5)
    fig_hist[i].show()

- The book has high pages tend to use hardcover, low pages using paperback.
- Hardcover has relative higher rating. Over half of the book's rating is close to 4.
- Most of the books' price are within $100

In [155]:
fig_scatmat = go.Figure(data=go.Splom(
                        dimensions=[dict(label=feature, values=book_data[feature]) \
                                    for feature in visualizable_feature_names], \
                        text=None,
                        marker=dict(color= None, showscale=False, line_color='white', line_width=0.5)))

fig_scatmat.update_layout(title='Pairwise feature scatter plots', \
                  width=400 * num_visualizable_features, \
                  height=400 * num_visualizable_features)

fig_scatmat.show()




Rating to price and number of pages does NOT have strong correlationship.
number of pages to the book price has low linear relationship. The higher pages the book has, the more likely the higher price it has.

Basically, it looks like they dont have strong relationship with books' rating.

> So, how to get higher rating?



#Decision Tree



> 1 hardcover  2Kindle  3paperback 4ebook else 5




> Rating considered:
- below 3 ->1
- 3 ~ 3.3 ->2
- 3.3 ~ 3.6 ->3
- 3.6 ~3.9 ->4
- 3.9 ~ 4.2 ->5
- above 4.2 ->6




In [395]:
from sklearn.tree import DecisionTreeClassifier
from sklearn.datasets import load_iris
from sklearn import preprocessing

feature = ['Number_Of_Pages','Type','Price']
x = book_data.loc[:,feature]

y = book_data.loc[:,['Rating']]

#transfer all book cover types from string to integer
def trans_Type_Data(a):
  if (a =='Hardcover' )| (a =='Boxed Set - Hardcover'):
    return 1
  if a == 'Kindle Edition':
    return 2
  if a == 'Paperback':
    return 3
  if a == 'ebook':
    return 4
  else :return 5


def trans_Rating(b):
  if b <= 3:
    return 1
  if (b > 3) & (b <= 3.3):
    return 2
  if (b > 3.3) & (b <= 3.6):
    return 3
  if (b > 3.6) & (b <= 3.9) :
    return 4
  if (b > 3.9) & (b <= 4.2):
    return 5
  if b > 4.2:
    return 6

#switch continous and string to integers

x['Type']=x['Type'].apply(trans_Type_Data)

y['Rating'] = y['Rating'].apply(trans_Rating)

display(x,y)



tree1 = DecisionTreeClassifier(criterion = "entropy", splitter = "random", max_depth = 6,  min_samples_split = 4,
                              min_samples_leaf = 2, max_features = 3)




Number_Of_Pages  Type       Price
0                105     1    9.323529
1                527     1   11.000000
2                 50     2   11.267647
3                393     1   12.873529
4                305     2   13.164706
..               ...   ...         ...
266              752     1  203.108823
267             1040     3  212.097059
268              896     1  220.385294
269             3168     1  220.385294
270              789     1  235.650000

[271 rows x 3 columns]

Rating
0         5
1         5
2         3
3         5
4         5
..      ...
266       4
267       5
268       6
269       6
270       4

[271 rows x 1 columns]

In [400]:
#select randomly from dataSet AS RATING TRUE, ref https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.train_test_split.html?highlight=test#sklearn.model_selection.train_test_split
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(x, y, test_size= 0.2, random_state= 42)

tree1.fit(X_train,y_train)

a= tree1.score(X_train,y_train)
print(a)

0.5833333333333334


 - meidum score

In [207]:
!pip install graphviz # install in collarb

In [401]:
from sklearn.tree import export_graphviz


export_graphviz(tree1, out_file='tree1.dot', 
                feature_names = feature,
                class_names = None,
                rounded = True, proportion = False, 
                precision = 2, filled = True)

# Convert to png using system command (requires Graphviz)
from subprocess import call
call(['dot', '-Tpng', 'tree1.dot', '-o', 'tree1.png', '-Gdpi=600'])

# Display in jupyter notebook
from IPython.display import Image
Image(filename = 'tree1.png')

According to this complicated decision tree, it shows some issues 
- raw data set is too small
- raw data is biased

#Prediction

In [408]:
#number of page, type, price

#try scenior page 2434, hardcover, and price 129 and 439 repectively
print("Book 1: 234 pages, hardcover, $29. Rating:",int(tree1.predict([[234, 2, 29]])))

print("Book 1: 234 pages, hardcover, $439. Rating:",int(tree1.predict([[234, 2, 439]])))


Book 1: 234 pages, hardcover, $29. Rating: 4
Book 1: 234 pages, hardcover, $439. Rating: 4


It's interesting to see the books has the same pages and cover, having the same rating. 

In [409]:
#score of the tree
tree1.score(x,y) 

#predict y
from sklearn.metrics import accuracy_score
y_test_predic = tree1.predict(X_test)
display(y_test_predic)

print("The accuracy is ", accuracy_score(y_test, y_test_predic)*100, "%")

array([5, 5, 5, 6, 6, 6, 5, 5, 5, 5, 6, 3, 5, 5, 5, 6, 6, 5, 4, 5, 5, 4,
       5, 4, 6, 4, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 6, 5, 5, 6, 5, 5,
       5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5])

The accuracy is  32.72727272727273 %


The Decision Tree is 2% accuracy.

In [404]:
# Try Building  Random Forest Classifier
from sklearn.ensemble import RandomForestClassifier
tree2 = RandomForestClassifier(criterion = 'entropy', n_estimators = 100, random_state = 42)
tree2.fit(X_train, y_train)

# Evaluating on Training set
rfc_pred_train =tree2.predict(X_train)

y2_test_predic = tree2.predict(X_test)
display(y_test_predic)

print("The accuracy is ", accuracy_score(y_test, y_test_predic)*100, "%")

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:4: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().



array([5, 5, 5, 6, 6, 6, 5, 5, 5, 5, 6, 3, 5, 5, 5, 6, 6, 5, 4, 5, 5, 4,
       5, 4, 6, 4, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 6, 5, 5, 6, 5, 5,
       5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5])

The accuracy is  32.72727272727273 %


#Conclusion

For this scenario, books' rating can not  correctly be predicted by its price, cover and its pages. All the graphs show that they dont have strong correlationship. 

Some possible related elements is missing: quality of books content, font size, color setting...

